In [2]:
! pip install sktime
! pip install standard-precip
import pandas as pd
import numpy as np

from datetime import datetime
import glob
import xarray as xr
import os
import matplotlib.pyplot as plt
from statsmodels.tsa.arima.model import ARIMA
from statsmodels.tsa.stattools import adfuller
from statsmodels.graphics.tsaplots import plot_acf, plot_pacf
import statsmodels.api as sm

from statsmodels.tsa.holtwinters import SimpleExpSmoothing, ExponentialSmoothing 

from sklearn.linear_model import LinearRegression

from sktime.transformations.series.detrend import Detrender
from sktime.forecasting.trend import PolynomialTrendForecaster
from sktime.utils.plotting import plot_series

from scipy.stats import gamma

from standard_precip.spi import SPI
from standard_precip.utils import plot_index

import seaborn as sns

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 21.9/21.9 MB 69.8 MB/s eta 0:00:00:00:0100:01
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 128.8/128.8 kB 9.1 MB/s eta 0:00:00


/opt/conda/lib/python3.10/site-packages/dask/dataframe/_pyarrow_compat.py:23: UserWarning: You are using pyarrow version 11.0.0 which is known to be insecure. See https://www.cve.org/CVERecord?id=CVE-2023-47248 for further details. Please upgrade to pyarrow>=14.0.1 or install pyarrow-hotfix to patch your current version.
  warnings.warn(


In [3]:
#read dataframe 
canola_2 = df = pd.read_csv('/kaggle/input/rm-yields-data/rm-yields-data.csv', header=0, index_col=0, parse_dates=True)
canola_small = canola_2.iloc[:, [0, 2]].copy()

#read dataframe 
#canola_2 = df = pd.read_csv('../data/rm-yields-data.csv', header=0, index_col=0, parse_dates=True)
#canola_small = canola_2.iloc[:, [0, 2]].copy()

In [4]:
start_year = 1938
start_analysis = 1990
exclude_years = start_analysis - start_year
#cut 70s and 80s as well 
#cut of first 52 observations (NAs)
canola_small.drop(canola_small.index[:exclude_years], inplace=True)

#filter out every observation that contains NAs
canola_filtered = canola_small.groupby('RM').filter(lambda group: not group['Canola'].isnull().any())

# how may districts? 148
num_districts = canola_filtered.groupby('RM').ngroups
print(num_districts)
#excluding 70s and 80s lead to 36 more colmplete districts 

184


In [5]:
# Group by 'RM' and check if 'Canola' has any missing values in each group
districts_with_full_data = canola_filtered.groupby('RM')['Canola'].apply(lambda group: not group.isnull().any())

# Extract the list of districts with full data
districts_with_full_data_list = districts_with_full_data[districts_with_full_data].index.tolist()

In [6]:
# select weather data
#open only the years from 1990 til 2022

# Define the directory path and pattern for the NetCDF files
directory_path = '/kaggle/input/copernicus-data/'
file_pattern = '*.nc'
# directory_path = '../data/all_raw_data/'
# file_pattern = 'data_*.nc'


# Get a list of files matching the pattern
files_to_open = glob.glob(os.path.join(directory_path, file_pattern))

# Open only the files for the years 1990 to 2022
years_to_open = list(map(str, range(start_analysis, 2023)))
files_to_open = [file for file in files_to_open if any(year in file for year in years_to_open)]

# Use open_mfdataset to open the selected files
cop_all_90 = xr.open_mfdataset(files_to_open, combine='by_coords')


# open data from 1971 til 1989 as training data 

training_years_to_open = list(map(str, range(1971, 1989)))
training_files_to_open = [file for file in files_to_open if any(year in file for year in years_to_open)]

# Use open_mfdataset to open the selected files
training_data = xr.open_mfdataset(training_files_to_open, combine='by_coords')

In [7]:
print(training_data)

<xarray.Dataset> Size: 5GB
Dimensions:    (longitude: 88, latitude: 41, time: 169488)
Coordinates:
  * longitude  (longitude) float32 352B -110.0 -109.9 -109.8 ... -101.4 -101.3
  * latitude   (latitude) float32 164B 53.0 52.9 52.8 52.7 ... 49.2 49.1 49.0
  * time       (time) datetime64[ns] 1MB 1990-04-01 ... 2022-10-31T23:00:00
Data variables:
    t2m        (time, latitude, longitude) float32 2GB dask.array<chunksize=(5136, 41, 88), meta=np.ndarray>
    tp         (time, latitude, longitude) float32 2GB dask.array<chunksize=(5136, 41, 88), meta=np.ndarray>
Attributes:
    Conventions:  CF-1.6
    history:      2024-01-23 18:32:47 GMT by grib_to_netcdf-2.24.0: /opt/ecmw...


In [8]:
# # center points for regions
df_regions = pd.read_csv('/kaggle/input/cgn-sk-csv-eng/cgn_sk_csv_eng.csv')
df_rms = df_regions[['Geographical Name','Latitude', 'Longitude']][df_regions['Generic Term'] == 'Rural Municipality']
df_rms['region_index'] = df_rms['Geographical Name'].str.split(' ').str[-1].astype(int)

# center points for regions
# df_regions = pd.read_csv(r'../data/cgn_sk_csv_eng.csv')
# df_rms = df_regions[['Geographical Name','Latitude', 'Longitude']][df_regions['Generic Term'] == 'Rural Municipality']
# df_rms['region_index'] = df_rms['Geographical Name'].str.split(' ').str[-1].astype(int)

In [9]:
#print(df_rms)

In [10]:
def get_center(region):
    avg_lat = df_rms['Latitude'][df_rms['region_index'] == region].item()
    avg_long = df_rms['Longitude'][df_rms['region_index'] == region].item()
    return avg_lat, avg_long

def detrend_ts(df_region):
    # linear detrending
    forecaster = PolynomialTrendForecaster(degree=2)
    transformer = Detrender(forecaster=forecaster)
    yt = transformer.fit_transform(df_region['Canola'])
    return yt

In [11]:
def merge_canola_weather_data(region = 310):
    # select data from region with center point
    center_lat, center_long = get_center(region)
    cropped_data_tmp = cop_all_90.sel(longitude=center_long, latitude=center_lat,method='nearest')
    cropped_data_tmp_train = training_data.sel(longitude=center_long, latitude=center_lat,method='nearest')
    
    # get residuals for canola yield
    df_tmp = canola_filtered[canola_filtered['RM'] == region]
    residuals = detrend_ts(df_tmp)

    # merge weather data and canola residuals
    df_weather_region = cropped_data_tmp.to_dataframe()
    df_weather_region_train = cropped_data_tmp_train.to_dataframe()

    df_weather_region['region'] = region

    column_to_append = residuals.tolist()
    years = df_weather_region.index.year
    df_weather_region['Canola_detrended'] = [column_to_append[year - start_analysis] for year in years]
    df_weather_region.drop(['longitude','latitude'],axis=1,inplace=True)
    
    df_weather_region_train['region'] = region

    column_to_append = residuals.tolist()
    years = df_weather_region_train.index.year
    df_weather_region_train['Canola_detrended'] = [column_to_append[year - start_analysis] for year in years]
    df_weather_region_train.drop(['longitude','latitude'],axis=1,inplace=True)

    return df_weather_region, pd.DataFrame(residuals), df_weather_region_train

In [12]:
def calculate_spi(prcp_data, scale=1):
    # Step 1: Calculate L-moments
    n = len(prcp_data)
    prcp_data_sorted = np.sort(prcp_data)
    
    # L-moment ratio
    l_moment_1 = np.sum(prcp_data_sorted) / n
    l_moment_2 = np.sum((2 * np.arange(1, n + 1) - 1 - n) * prcp_data_sorted) / (n ** 2)
    
    # Step 2: Estimate parameters of gamma distribution
    k = l_moment_1 / l_moment_2
    theta = l_moment_2 / k
    
    # Step 3: Calculate SPI values
    spi_values = gamma.ppf((np.arange(1, n + 1) - 0.35) / (n + 0.3), a=k, scale=theta * scale)
    
    return spi_values

In [13]:
def calc_temp_features(df_weather_region, df_year):
    for month in range(4,11):    
        daily_max_temperatures = df_weather_region.resample('D').max()
        monthly_avg_max_temperatures = daily_max_temperatures.resample('MS').mean()
        
    #     dist1_df_month = dist1_df.resample('MS').mean()
        month_data = monthly_avg_max_temperatures[monthly_avg_max_temperatures.index.month == month]
        column_to_append = month_data['t2m'].tolist()
        df_year.loc[:, f'average_max_temp_in_{month}'] = column_to_append
    return df_year

In [14]:
def calc_spi_features(df_weather_region, df_year):
    for month in range(4, 11):
        # tried resampling in various ways but none worked
        tp_in_month = df_weather_region[df_weather_region.index.month == month]

        spi = SPI()

        # Assuming spi.calculate is the SPI calculation function
        spi_values = spi.calculate(
            tp_in_month.reset_index(),
            'time',
            'tp',
            freq="M",
            scale=1,
            fit_type="lmom",
            dist_type="gam"
        )
        
        # may have to aggregate here somehow

        # Add each SPI column separately
        for col_name in spi_values.columns:
            df_year[f'SPI_in_{month}_{col_name}'] = spi_values[col_name]
            
    return df_year

In [15]:
def calc_summer_days(df_weather_region, df_year):

    testing_data = df_weather_region['t2m'].resample('D').max()
    testing_data = testing_data.dropna()
    test_df_summer = testing_data.to_frame(name='t2m')
    test_df_summer['month_day'] = test_df_summer.index.strftime('%m-%d')
    test_df_summer['above_25'] = test_df_summer['t2m'] > 298
    days_over_25 = test_df_summer.groupby(test_df_summer.index.year)['above_25'].apply(sum)
    column_to_append = days_over_25.tolist()
    df_year.loc[:, f'days_above_25'] = column_to_append
    
    return df_year

In [16]:
def calc_frost_days(df_weather_region, df_year):

    testing_data = df_weather_region['t2m'].resample('D').max()
    testing_data = testing_data.dropna()
    test_df_frost = testing_data.to_frame(name='t2m')
    test_df_frost['month_day'] = test_df_frost.index.strftime('%m-%d')
    test_df_frost['under_0'] = test_df_frost['t2m'] < 273
    days_under_0 = test_df_frost.groupby(test_df_frost.index.year)['under_0'].apply(sum)
    column_to_append = days_under_0.tolist()
    df_year.loc[:, f'days_under_0'] = column_to_append
    
    return df_year

In [17]:
# function to calculate the longest consecutive true streak

def longest_consecutive_true_streak(series):
    
    # Convert the series to integers (True to 1, False to 0) for easier streak calculation
    as_ints = series.astype(int)
    # Calculate the difference to identify changes in streaks
    diff = as_ints.diff()
    # Start a new group every time there's a change from 0 to 1 (start of a new streak)
    groups = (diff == 1).cumsum()
    # Use the groups to isolate consecutive trues, then count them, keeping the max
    streak_lengths = as_ints.groupby(groups).sum()
    # Return the length of the longest streak
    return streak_lengths.max()

In [18]:
def longest_dry_spell(df_weather_region, df_year):
    
    dist1_df_perci = df_weather_region.resample('D').sum()
    dist1_df_perci_wo0 = dist1_df_perci[dist1_df_perci['tp'] != 0].copy()
    
    # Threshhold is 1mm or 0.001m, here precipitation is likely measured in m 
    
    dist1_df_perci_wo0.loc[:,'less_than_0.001'] = dist1_df_perci_wo0['tp'] < 0.001
    longest_dry_spell_per_year = dist1_df_perci_wo0.groupby(dist1_df_perci_wo0.index.year)['less_than_0.001'].apply(longest_consecutive_true_streak)
    
    column_to_append = longest_dry_spell_per_year.tolist()
    df_year.loc[:, f'longest_dry_spell'] = column_to_append
    
    return df_year

In [19]:
def longest_wet_spell(df_weather_region, df_year):
    
    dist1_df_perci = df_weather_region.resample('D').sum()
    dist1_df_perci_wo0 = dist1_df_perci[dist1_df_perci['tp'] != 0].copy()
    
    # Threshhold is 1mm or 0.001m, here precipitation is likely measured in m 
    
    dist1_df_perci_wo0.loc[:,'more_than_0.001'] = dist1_df_perci_wo0['tp'] > 0.001
    longest_wet_spell_per_year = dist1_df_perci_wo0.groupby(dist1_df_perci_wo0.index.year)['more_than_0.001'].apply(longest_consecutive_true_streak)
    
    column_to_append = longest_wet_spell_per_year.tolist()
    df_year.loc[:, f'longest_wet_spell'] = column_to_append
    
    return df_year

In [20]:
def over_95_precipitation(df_weather_region, df_weather_region_train, df_year):
    
    dist1_df_perci = df_weather_region.resample('D').sum()
    dist1_df_perci_wo0 = dist1_df_perci[dist1_df_perci['tp'] != 0]
    testing_data_pre = dist1_df_perci_wo0["tp"]
    
    dist1_df_perci_train = df_weather_region_train.resample('D').sum()
    dist1_df_perci_wo0_train = dist1_df_perci_train[dist1_df_perci_train['tp'] != 0]
    training_data_pre = dist1_df_perci_wo0_train["tp"]


    # calculate for every day the 90% quantile
    quantile_95_series = training_data_pre.groupby([training_data_pre.index.month, training_data_pre.index.day]).quantile(0.95)
    quantile_95_series.index = quantile_95_series.index.map(lambda x: f"{x[0]:02d}-{x[1]:02d}")

    test_df_pre = testing_data_pre.to_frame(name='tp')
    test_df_pre['month_day'] = test_df_pre.index.strftime('%m-%d')

    # map the 90th percentile values from quantile_90_series to the test series
    test_df_pre['quantile_95'] = test_df_pre['month_day'].apply(lambda x: quantile_95_series.get(x, pd.NA))

    # compare each test value to its corresponding 90th percentile value
    test_df_pre['over_quantile_95'] = test_df_pre['tp'] > test_df_pre['quantile_95']
    test_df_pre.drop(['month_day', 'quantile_95'], axis=1, inplace=True)

    # Group the DataFrame by year, and apply the function to find the longest streak of True values
    days_over_95 = test_df_pre.groupby(test_df_pre.index.year)['over_quantile_95'].apply(sum)

    column_to_append = days_over_95.tolist()
    df_year.loc[:, f'days_over_95_precipitation'] = column_to_append
    
    return df_year

In [21]:
def heat_wave(df_weather_region, df_weather_region_train, df_year):

    training_data = df_weather_region_train['t2m'].resample('D').max()
    training_data = training_data.dropna()

    testing_data = df_weather_region['t2m'].resample('D').max()
    testing_data = testing_data.dropna()

    # calculate for every day the 90% quantile
    quantile_90_series = training_data.groupby([training_data.index.month, training_data.index.day]).quantile(0.9)
    quantile_90_series.index = quantile_90_series.index.map(lambda x: f"{x[0]:02d}-{x[1]:02d}")

    test_df = testing_data.to_frame(name='value')
    test_df['month_day'] = test_df.index.strftime('%m-%d')

    # map the 90th percentile values from quantile_90_series to the test series
    test_df['quantile_90'] = test_df['month_day'].apply(lambda x: quantile_90_series.get(x, pd.NA))

    # compare each test value to its corresponding 90th percentile value
    test_df['is_above_quantile_90'] = test_df['value'] > test_df['quantile_90']
    test_df.drop(['month_day', 'quantile_90'], axis=1, inplace=True)

    # Group the DataFrame by year, and apply the function to find the longest streak of True values
    longest_heat_streak_by_year = test_df.groupby(test_df.index.year)['is_above_quantile_90'].apply(longest_consecutive_true_streak)

    column_to_append = longest_heat_streak_by_year.tolist()
    df_year.loc[:, f'longest_heat_wave'] = column_to_append
    
    return df_year

In [22]:
def cold_wave(df_weather_region, df_weather_region_train, df_year):
    
    training_data = df_weather_region_train['t2m'].resample('D').min()
    training_data = training_data.dropna()

    testing_data = df_weather_region['t2m'].resample('D').min()
    testing_data = testing_data.dropna()
    
    # calculate for every day the 90% quantile
    quantile_10_series = training_data.groupby([training_data.index.month, training_data.index.day]).quantile(0.1)
    quantile_10_series.index = quantile_10_series.index.map(lambda x: f"{x[0]:02d}-{x[1]:02d}")

    test_df_cold = testing_data.to_frame(name='value')
    test_df_cold['month_day'] = test_df_cold.index.strftime('%m-%d')

    # map the 90th percentile values from quantile_90_series to the test series
    test_df_cold['quantile_10'] = test_df_cold['month_day'].apply(lambda x: quantile_10_series.get(x, pd.NA))

    # compare each test value to its corresponding 90th percentile value
    test_df_cold['is_under_quantile_10'] = test_df_cold['value'] < test_df_cold['quantile_10']
    test_df_cold.drop(['month_day', 'quantile_10'], axis=1, inplace=True)

    # Group the DataFrame by year, and apply the function to find the longest streak of True values
    longest_streak_by_year_cold = test_df_cold.groupby(test_df_cold.index.year)['is_under_quantile_10'].apply(longest_consecutive_true_streak)

    column_to_append = longest_streak_by_year_cold.tolist()
    df_year.loc[:, f'longest_cold_wave'] = column_to_append
    
    return df_year

In [23]:
available_regions = [region for region in districts_with_full_data_list if region in df_rms['region_index'].to_list()]

In [24]:
available_regions.remove(278)
available_regions.remove(529)

In [28]:
dfs_of_years = []
for region in available_regions:
    print(region)
    df_weather_region, df_year, df_weather_region_train  = merge_canola_weather_data(region)
    df_year.index = df_year.index.year
    df_year['region'] = region
    df_year = calc_temp_features(df_weather_region, df_year)
    df_year = calc_summer_days(df_weather_region,df_year)
    df_year = calc_frost_days(df_weather_region,df_year)
    df_year = longest_dry_spell(df_weather_region,df_year)
    df_year = longest_wet_spell(df_weather_region,df_year)
    df_year = over_95_precipitation(df_weather_region, df_weather_region_train, df_year)
    df_year = heat_wave(df_weather_region, df_weather_region_train, df_year)
    df_year = cold_wave(df_weather_region, df_weather_region_train, df_year)
    dfs_of_years.append(df_year)

1


/tmp/ipykernel_34/3396280033.py:8: FutureWarning: The provided callable <built-in function sum> is currently using np.sum. In a future version of pandas, the provided callable will be used directly. To keep current behavior pass the string np.sum instead.
  days_over_25 = test_df_summer.groupby(test_df_summer.index.year)['above_25'].apply(sum)
/tmp/ipykernel_34/2713775003.py:8: FutureWarning: The provided callable <built-in function sum> is currently using np.sum. In a future version of pandas, the provided callable will be used directly. To keep current behavior pass the string np.sum instead.
  days_under_0 = test_df_frost.groupby(test_df_frost.index.year)['under_0'].apply(sum)
/tmp/ipykernel_34/3488170437.py:12: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  streak_lengths = as_ints.groupby(groups).

2


/tmp/ipykernel_34/3396280033.py:8: FutureWarning: The provided callable <built-in function sum> is currently using np.sum. In a future version of pandas, the provided callable will be used directly. To keep current behavior pass the string np.sum instead.
  days_over_25 = test_df_summer.groupby(test_df_summer.index.year)['above_25'].apply(sum)
/tmp/ipykernel_34/2713775003.py:8: FutureWarning: The provided callable <built-in function sum> is currently using np.sum. In a future version of pandas, the provided callable will be used directly. To keep current behavior pass the string np.sum instead.
  days_under_0 = test_df_frost.groupby(test_df_frost.index.year)['under_0'].apply(sum)
/tmp/ipykernel_34/3488170437.py:12: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  streak_lengths = as_ints.groupby(groups).

3


...

/tmp/ipykernel_34/3396280033.py:8: FutureWarning: The provided callable <built-in function sum> is currently using np.sum. In a future version of pandas, the provided callable will be used directly. To keep current behavior pass the string np.sum instead.
  days_over_25 = test_df_summer.groupby(test_df_summer.index.year)['above_25'].apply(sum)
/tmp/ipykernel_34/2713775003.py:8: FutureWarning: The provided callable <built-in function sum> is currently using np.sum. In a future version of pandas, the provided callable will be used directly. To keep current behavior pass the string np.sum instead.
  days_under_0 = test_df_frost.groupby(test_df_frost.index.year)['under_0'].apply(sum)
/tmp/ipykernel_34/3488170437.py:12: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  streak_lengths = as_ints.groupby(groups).

588


/tmp/ipykernel_34/3396280033.py:8: FutureWarning: The provided callable <built-in function sum> is currently using np.sum. In a future version of pandas, the provided callable will be used directly. To keep current behavior pass the string np.sum instead.
  days_over_25 = test_df_summer.groupby(test_df_summer.index.year)['above_25'].apply(sum)
/tmp/ipykernel_34/2713775003.py:8: FutureWarning: The provided callable <built-in function sum> is currently using np.sum. In a future version of pandas, the provided callable will be used directly. To keep current behavior pass the string np.sum instead.
  days_under_0 = test_df_frost.groupby(test_df_frost.index.year)['under_0'].apply(sum)
/tmp/ipykernel_34/3488170437.py:12: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  streak_lengths = as_ints.groupby(groups).

622


/tmp/ipykernel_34/3396280033.py:8: FutureWarning: The provided callable <built-in function sum> is currently using np.sum. In a future version of pandas, the provided callable will be used directly. To keep current behavior pass the string np.sum instead.
  days_over_25 = test_df_summer.groupby(test_df_summer.index.year)['above_25'].apply(sum)
/tmp/ipykernel_34/2713775003.py:8: FutureWarning: The provided callable <built-in function sum> is currently using np.sum. In a future version of pandas, the provided callable will be used directly. To keep current behavior pass the string np.sum instead.
  days_under_0 = test_df_frost.groupby(test_df_frost.index.year)['under_0'].apply(sum)
/tmp/ipykernel_34/3488170437.py:12: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  streak_lengths = as_ints.groupby(groups).

In [29]:
df_full = pd.concat(dfs_of_years)

In [30]:
df_full

Canola  region  average_max_temp_in_4  average_max_temp_in_5  \
Year                                                                    
1990   0.127132       1             284.965759             290.526489   
1991   2.520378       1             287.648346             291.984650   
1992  -6.339489       1             283.242584             293.701874   
1993   4.147971       1             284.697113             292.762695   
1994   2.081733       1             285.144440             293.432678   
...         ...     ...                    ...                    ...   
2018  -0.642088     622             277.338013             294.617126   
2019   5.176214     622             283.511230             289.193604   
2020  -1.002221     622             277.344818             290.024719   
2021 -18.980060     622             284.660583             290.581299   
2022   0.548040     622             279.618134             289.977875   

      average_max_temp_in_6  average_max_temp_in_7  average_max_temp_in_8  \
Year                                                                        
1990             297.082458             299.412781             300.752075   
1991             296.854401             297.652344             299.938751   
1992             295.445709             294.548126             297.033264   
1993             293.425385             294.037415             296.177429   
1994             294.774536             297.061951             297.072021   
...                     ...                    ...                    ...   
2018             296.039825             297.508179             297.946716   
2019             293.939178             295.673492             293.541107   
2020             293.347931             296.085846             296.669983   
2021             297.739471             299.774323             298.133942   
2022             294.012695             296.951447             298.845917   

      average_max_temp_in_9  average_max_temp_in_10  days_above_25  \
Year                                                                 
1990             296.791382              286.036377             72   
1991             292.543549              282.321960             51   
1992             292.229004              285.503967             37   
1993             291.031281              284.688232             26   
1994             294.903839              286.052094             38   
...                     ...                     ...            ...   
2018             285.104767              280.153503             51   
2019             289.933136              280.083069             11   
2020             291.383881              279.867188             23   
2021             293.659637              284.803772             55   
2022             295.413269              287.941833             41   

      days_under_0  longest_dry_spell  longest_wet_spell  \
Year                                                       
1990             0                  7                 11   
1991             4                  6                 13   
1992             2                  7                 11   
1993             1                  6                 14   
1994             0                  9                 15   
...            ...                ...                ...   
2018            11                  9                 20   
2019             3                  7                 33   
2020            17                  6                 10   
2021             0                 17                 10   
2022             5                 18                 22   

      days_over_95_precipitation  longest_heat_wave  longest_cold_wave  
Year                                                                    
1990                          11                  7                  5  
1991                          18                  6                  4  
1992                           8                  5                  7  


In [32]:
files_dir = '/kaggle/input/all-spi-features'
!ls $files_dir

Reg1.csv    Reg214.csv	Reg277.csv  Reg336.csv	Reg404.csv  Reg467.csv
Reg121.csv  Reg216.csv	Reg280.csv  Reg337.csv	Reg405.csv  Reg468.csv
Reg122.csv  Reg217.csv	Reg281.csv  Reg338.csv	Reg406.csv  Reg471.csv
Reg123.csv  Reg218.csv	Reg282.csv  Reg339.csv	Reg409.csv  Reg472.csv
Reg124.csv  Reg219.csv	Reg283.csv  Reg34.csv	Reg410.csv  Reg486.csv
Reg125.csv  Reg220.csv	Reg284.csv  Reg340.csv	Reg411.csv  Reg487.csv
Reg126.csv  Reg221.csv	Reg288.csv  Reg341.csv	Reg426.csv  Reg488.csv
Reg127.csv  Reg222.csv	Reg3.csv    Reg342.csv	Reg427.csv  Reg490.csv
Reg131.csv  Reg223.csv	Reg304.csv  Reg343.csv	Reg428.csv  Reg491.csv
Reg151.csv  Reg224.csv	Reg305.csv  Reg344.csv	Reg429.csv  Reg493.csv
Reg152.csv  Reg225.csv	Reg307.csv  Reg372.csv	Reg430.csv  Reg494.csv
Reg153.csv  Reg241.csv	Reg308.csv  Reg373.csv	Reg431.csv  Reg497.csv
Reg154.csv  Reg243.csv	Reg309.csv  Reg376.csv	Reg435.csv  Reg499.csv
Reg155.csv  Reg244.csv	Reg31.csv   Reg377.csv	Reg436.csv  Reg501.csv
Reg156.csv  Reg245.csv	Reg310.csv  

In [42]:
files = glob.glob(os.path.join(files_dir, "*.csv"))

# Make a list of dataframes while adding a tag column
dataframes = [pd.read_csv(file) for file in files]
# Concatenate all the dataframes into one
spis_df = pd.concat(dataframes, ignore_index=False)

In [43]:
spis_df

Year  SPI_in_4  SPI_in_5  SPI_in_6  SPI_in_7  SPI_in_8  SPI_in_9  \
0   1990  0.007363  0.181660  0.239990  0.265157  0.214480  0.068857   
1   1991  0.242713  0.340260  0.129390  0.199950 -0.042113  0.317139   
2   1992  0.105582  0.188406 -0.135033  0.309609  0.253276  0.486380   
3   1993  0.076444 -0.163913  0.104482  0.392346  0.329518  0.599675   
4   1994 -0.099591  0.047024  0.495226  0.184224  0.319721 -0.127680   
..   ...       ...       ...       ...       ...       ...       ...   
29  2019  0.106943  0.006460  0.298540  0.309699  0.283975  0.300908   
30  2020  0.218784  0.175136  0.270534  0.246509 -0.180080  0.226821   
31  2021 -0.189378 -0.138437 -0.117233 -0.477873  0.292438  0.226422   
32  2022  0.219583  0.363215  0.019326 -0.081898  0.115568 -0.059107   
33  2023  0.076061 -0.242731 -0.172470 -0.102800  0.339795  0.021867   

    SPI_in_10  Region  Soil Zone  
0    0.017782     214          1  
1    0.419316     214          1  
2   -0.043126     214          1  
3   -0.107177     214          1  
4    0.058529     214          1  
..        ...     ...        ...  
29   0.154892     520          1  
30   0.184991     520          1  
31  -0.244333     520          1  
32  -0.245435     520          1  
33   0.242165     520          1  

[5712 rows x 10 columns]

In [45]:
spis_df.set_index('Year', inplace=True)

In [46]:
merged_df = pd.merge(df_full, spis_df, how='left', left_on=['Year', 'region'], right_on=['Year', 'Region'])
merged_df

Canola  region  average_max_temp_in_4  average_max_temp_in_5  \
Year                                                                    
1990   0.127132       1             284.965759             290.526489   
1991   2.520378       1             287.648346             291.984650   
1992  -6.339489       1             283.242584             293.701874   
1993   4.147971       1             284.697113             292.762695   
1994   2.081733       1             285.144440             293.432678   
...         ...     ...                    ...                    ...   
2018  -0.642088     622             277.338013             294.617126   
2019   5.176214     622             283.511230             289.193604   
2020  -1.002221     622             277.344818             290.024719   
2021 -18.980060     622             284.660583             290.581299   
2022   0.548040     622             279.618134             289.977875   

      average_max_temp_in_6  average_max_temp_in_7  average_max_temp_in_8  \
Year                                                                        
1990             297.082458             299.412781             300.752075   
1991             296.854401             297.652344             299.938751   
1992             295.445709             294.548126             297.033264   
1993             293.425385             294.037415             296.177429   
1994             294.774536             297.061951             297.072021   
...                     ...                    ...                    ...   
2018             296.039825             297.508179             297.946716   
2019             293.939178             295.673492             293.541107   
2020             293.347931             296.085846             296.669983   
2021             297.739471             299.774323             298.133942   
2022             294.012695             296.951447             298.845917   

      average_max_temp_in_9  average_max_temp_in_10  days_above_25  ...  \
Year                                                                ...   
1990             296.791382              286.036377             72  ...   
1991             292.543549              282.321960             51  ...   
1992             292.229004              285.503967             37  ...   
1993             291.031281              284.688232             26  ...   
1994             294.903839              286.052094             38  ...   
...                     ...                     ...            ...  ...   
2018             285.104767              280.153503             51  ...   
2019             289.933136              280.083069             11  ...   
2020             291.383881              279.867188             23  ...   
2021             293.659637              284.803772             55  ...   
2022             295.413269              287.941833             41  ...   

      longest_cold_wave  SPI_in_4  SPI_in_5  SPI_in_6  SPI_in_7  SPI_in_8  \
Year                                                                        
1990                  5  0.091579  0.029108  0.115236  0.209242  0.256968   
1991                  4  0.331210  0.331767  0.195163  0.282696  0.222439   
1992                  7  0.144230  0.193160 -0.188189  0.358708  0.309846   
1993                  5  0.115240 -0.052129  0.086120  0.608185  0.263007   
1994                  6 -0.063990  0.114090  0.446020  0.102491  0.320304   
...                 ...       ...       ...       ...       ...       ...   
2018                  9 -0.031262  0.071520 -0.122097  0.151804  0.051411   
2019                  4  0.081506 -0.011202  0.415322  0.431917  0.398095   
2020                 11  0.007929  0.199944  0.051762  0.370352 -0.142280   
2021                  3 -0.371442  0.136880 -0.346204 -0.245956  0.046748   
2022                  4  0.432467  0.204122 -0.051296  0.081554 -0.135292   

      SPI_in_9  SPI_in_10  Region  Soil Zone  
Year                            

In [47]:
merged_df.to_csv('full_feature_df.csv', index=True)